In [0]:
from pyspark.sql import SparkSession
from pyspark.ml.feature import VectorAssembler, StringIndexer
from pyspark.ml.classification import DecisionTreeClassifier
from pyspark.ml import Pipeline
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
import matplotlib.pyplot as plt
import pandas as pd
import seaborn as sns

# Crear una sesión de Spark
spark = SparkSession.builder.appName("ClasificacionVehiculos").getOrCreate()


# Convertir CRASH_TIME en una característica numérica (hora en formato de 24 horas)
from pyspark.sql.functions import hour, minute, udf
from pyspark.sql.types import IntegerType

# Extraer la hora y minuto de CRASH_TIME
get_hour = udf(lambda time: int(time.split(':')[0]), IntegerType())
get_minute = udf(lambda time: int(time.split(':')[1]), IntegerType())
df3I = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/juanjoserodriguezcubillos@gmail.com/Collisions_modified.csv")
df3I = df3I.withColumn("HOUR", get_hour(df3I["CRASH_TIME"]))
df3I = df3I.withColumn("MINUTE", get_minute(df3I["CRASH_TIME"]))

# Convertir HOUR y MINUTE a un solo valor numérico
df3I = df3I.withColumn("TIME_NUMERIC", df3I["HOUR"] + df3I["MINUTE"] / 60.0)

# Indexar VEHICLE_TYPE (columna objetivo)
vehicle_type_indexer = StringIndexer(inputCol="VEHICLE_TYPE", outputCol="vehicle_type_index").fit(df3I)

# Aplicar el indexador
df3I = vehicle_type_indexer.transform(df3I)

# Eliminar cualquier columna existente llamada 'label' o 'features'
df3I = df3I.drop("label", "features")

# Asegurarse de que la columna de la etiqueta es numérica y renombrar
df3I = df3I.withColumnRenamed("vehicle_type_index", "label")

# Ensamblar las características en un solo vector
assembler = VectorAssembler(
    inputCols=["TIME_NUMERIC"],
    outputCol="features")

df3I = assembler.transform(df3I)

# Dividir los datos en conjuntos de entrenamiento y prueba
(trainingData, testData) = df3I.randomSplit([0.8, 0.2], seed=42)

# Crear el modelo de Árbol de Decisión
dt = DecisionTreeClassifier(featuresCol="features", labelCol="label",maxDepth=10)

# Entrenar el modelo
model = dt.fit(trainingData)

# Hacer predicciones
predictions = model.transform(testData)

# Evaluar el modelo
evaluator = MulticlassClassificationEvaluator(labelCol="label", predictionCol="prediction", metricName="accuracy")
accuracy = evaluator.evaluate(predictions)
print(f"Accuracy en los datos de prueba: {accuracy}")

# Calcular la matriz de confusión
predictions_pd = predictions.select("prediction", "label").toPandas()
confusion_matrix = pd.crosstab(predictions_pd['label'], predictions_pd['prediction'], rownames=['Actual'], colnames=['Predicted'])

# Mostrar la matriz de confusión
plt.figure(figsize=(10, 7))
sns.heatmap(confusion_matrix, annot=True, fmt="d", cmap="YlGnBu")
plt.title("Matriz de Confusión")
plt.show()

# Cuadro de la evaluación del modelo utilizando pandas
evaluation_metrics = {
    "Metric": ["Accuracy"],
    "Value": [accuracy]
}

evaluation_df = pd.DataFrame(evaluation_metrics)
print(evaluation_df)

In [0]:
display(predictions)

CRASH_DATE CRASH_TIME STATE_REGISTRATION VEHICLE_TYPE VEHICLE_MAKE VEHICLE_YEAR TRAVEL_DIRECTION VEHICLE_OCCUPANTS PRE_CRASH POINT_OF_IMPACT VEHICLE_DAMAGE PUBLIC_PROPERTY_DAMAGE CONTRIBUTING_FACTOR_1 CONTRIBUTING_FACTOR_2 HOUR MINUTE TIME_NUMERIC label features rawPrediction probability prediction 01/01/2015 0:33 NY UNKNOWN TOYT -CAR/SUV 2014.0 West 1.0 Making Right Turn Center Front End Center Front End N Unspecified Unspecified 0 33 0.55 5.0 Map(vectorType -> dense, length -> 1, values -> List(0.55)) Map(vectorType -> dense, length -> 192, values -> List(754974.0, 359128.0, 228207.0, 215135.0, 138572.0, 91828.0, 59944.0, 47891.0, 47826.0, 30261.0, 28132.0, 27279.0, 26373.0, 24306.0, 22679.0, 19593.0, 18389.0, 13920.0, 12529.0, 11430.0, 8972.0, 7537.0, 6896.0, 6695.0, 3795.0, 3514.0, 2377.0, 2372.0, 1748.0, 1550.0, 1409.0, 1352.0, 1345.0, 1067.0, 1006.0, 745.0, 584.0, 550.0, 520.0, 444.0, 380.0, 368.0, 344.0, 285.0, 250.0, 267.0, 227.0, 221.0, 173.0, 172.0, 170.0, 156.0, 150.0, 133.0, 133.0, 109.0, 117.0, 83.0, 98.0, 93.0, 79.0, 86.0, 90.0, 97.0, 90.0, 64.0, 75.0, 69.0, 71.0, 73.0, 64.0, 64.0, 62.0, 72.0, 71.0, 47.0, 46.0, 41.0, 47.0, 46.0, 36.0, 46.0, 43.0, 45.0, 40.0, 47.0, 45.0, 46.0, 48.0, 48.0, 46.0, 44.0, 19.0, 22.0, 21.0, 19.0, 21.0, 23.0, 22.0, 22.0, 18.0, 21.0, 22.0, 23.0, 22.0, 17.0, 23.0, 22.0, 22.0, 23.0, 23.0, 22.0, 17.0, 19.0, 19.0, 21.0, 21.0, 24.0, 22.0, 24.0, 18.0, 25.0, 21.0, 22.0, 23.0, 21.0, 23.0, 22.0, 25.0, 21.0, 25.0, 24.0, 22.0, 19.0, 16.0, 23.0, 21.0, 21.0, 23.0, 22.0, 21.0, 18.0, 24.0, 23.0, 24.0, 21.0, 23.0, 24.0, 23.0, 24.0, 24.0, 21.0, 22.0, 20.0, 21.0, 26.0, 25.0, 25.0, 18.0, 24.0, 21.0, 21.0, 25.0, 19.0, 23.0, 25.0, 21.0, 22.0, 23.0, 20.0, 22.0, 28.0, 24.0, 21.0, 19.0, 21.0, 24.0, 24.0, 20.0, 22.0, 20.0, 23.0, 23.0, 22.0, 19.0, 20.0, 21.0, 16.0, 24.0, 23.0, 25.0, 27.0)) Map(vectorType -> dense, length -> 192, values -> List(0.3369094565931881, 0.1602619683954659, 0.10183807172268407, 0.09600465174188187, 0.06183817882341811, 0.040978525856571586, 0.0267501933391376, 0.021371505224953936, 0.02134249877615099, 0.013504063803477294, 0.012553991041916103, 0.012173337183009718, 0.011769031912002468, 0.010846626840068705, 0.010120573113877979, 0.008743436175325687, 0.008206147492883379, 0.006211842574416045, 0.005591104570032947, 0.005100672458733864, 0.004003782440923904, 0.0033634093019665034, 0.0030773610914635804, 0.0029876642267036937, 0.0016935303570336845, 0.0015681332475932456, 0.0010607435200709007, 0.001058512254778366, 7.800503462700607E-4, 6.916922406856946E-4, 6.287705594362217E-4, 6.033341351013284E-4, 6.002103636917801E-4, 4.7615201342686203E-4, 4.4893057685794113E-4, 3.324585285876403E-4, 2.6061178616802944E-4, 2.4543918217879486E-4, 2.3205159042358786E-4, 1.9813635797706348E-4, 1.695761622326219E-4, 1.642211255305391E-4, 1.535110521263735E-4, 1.2718212167446642E-4, 1.1156326462672494E-4, 1.1914956662134223E-4, 1.0129944428106623E-4, 9.862192593002485E-5, 7.720177912169366E-5, 7.675552606318675E-5, 7.586301994617296E-5, 6.961547712707636E-5, 6.693795877603496E-5, 5.9351656781417665E-5, 5.9351656781417665E-5, 4.8641583377252075E-5, 5.221160784530727E-5, 3.7039003856072676E-5, 4.3732799733676174E-5, 4.150153444114167E-5, 3.525399162204508E-5, 3.8377763031593376E-5, 4.016277526562098E-5, 4.328654667516928E-5, 4.016277526562098E-5, 2.8560195744441585E-5, 3.346897938801748E-5, 3.079146103697608E-5, 3.1683967153989885E-5, 3.257647327100368E-5, 2.8560195744441585E-5, 2.8560195744441585E-5, 2.7667689627427783E-5, 3.213022021249678E-5, 3.1683967153989885E-5, 2.097389374982429E-5, 2.0527640691317388E-5, 1.829637539878289E-5, 2.097389374982429E-5, 2.0527640691317388E-5, 1.606511010624839E-5, 2.0527640691317388E-5, 1.9188881515796688E-5, 2.008138763281049E-5, 1.785012234027599E-5, 2.097389374982429E-5, 2.008138763281049E-5, 2.0527640691317388E-5, 2.1420146808331186E-5, 2.1420146808331186E-5, 2.0527640691317388E-5, 1.963513457430359E-5, 8.478808111631095E-6, 9.817567287151795E-6, 9.371314228644895